In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{40}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/40)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [5.714187819929618e-21, 1.9204922375219092e-21, -1.9204922375219032e-21, -5.714187819929618e-21, -9.367181133908561e-21, -1.278952336047883e-20, -1.5896945075919605e-20], 'solu': -4.4647448282725816e-21}, {'input': [5.485352858619707e-05, 4.413115110528725e-05, 3.232211822127183e-05, 1.9717207515688445e-05, 6.626793723408747e-06, -6.626793723408726e-06, -1.971720751568844e-05], 'solu': 1.5405916476286106e-05}, {'input': [0.18183878984410332, 0.06111454425036399, -0.06111454425036442, -0.1818387898441051, -0.2980855609435391, -0.4069924762432843, -0.5058778860473319], 'solu': -0.1420785984150258}, {'input': [-0.00048741365791955685, -0.0007990097918989417, -0.0010909316530403074, -0.0013559911562892415, -0.001587661656993699, -0.0017802386585560248, -0.00192898027607133], 'solu': -0.0010594951886443791}, {'input': [9.394417377439692e-12, 5.730802531316246e-12, 1.926076307428645e-12, -1.926076307428649e-12, -5.730802531316272e-12, -9.394417377439715e-12, -1.2826710489446846e-1

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_12 xx.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_12 xx.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_xx delta x=1 20 delta t=1 40")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{40}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/40)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [-0.02968244004878135, -0.027438165350308238, -0.02502472523833462, -0.02245699937370112, -0.019750818640218642, -0.016922867542005574, -0.013990581337971505], 'solu': -0.017546635667549246}, {'input': [1.3789397129177673e-19, 1.3704380910436437e-19, 1.3534872626213266e-19, 1.3281917351447618e-19, 1.2947074639524597e-19, 1.2532408907109698e-19, 1.2040476706333615e-19], 'solu': 1.0377742852202927e-19}, {'input': [-8.247034562080435e-26, -8.350318923681297e-26, -8.402120792354849e-26, -8.402120792354847e-26, -8.350318923681295e-26, -8.247034562080433e-26, -8.092904489987063e-26], 'solu': -6.564944404408841e-26}, {'input': [1.5263811831216345e-24, 1.4109722523236438e-24, 1.2868642083941917e-24, 1.1548222186942161e-24, 1.0156603659986341e-24, 8.702366294053269e-25, 7.194475946086917e-25], 'solu': 9.023131004736102e-25}, {'input': [4.371153490146662e-12, 4.3442038753238725e-12, 4.29047079901533e-12, 4.210285543504539e-12, 4.10414247755603e-12, 3.972696008467524e-12, 3.81675654743

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_22 xx.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_22 xx.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_xx delta x=1 40 delta t=1 40")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{40}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/40)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [3.941342280274465e-21, 2.3672389005026945e-21, 7.894854099272559e-22, -7.8948540992724615e-22, -2.3672389005027024e-21, -3.941342280274482e-21, -5.509368395924247e-21], 'solu': -6.1685947540533365e-22}, {'input': [6.721543808793081e-09, 6.337737253164568e-09, 5.944158366060034e-09, 5.541414017596227e-09, 5.130125210366989e-09, 4.71092612190226e-09, 4.284463126812291e-09], 'solu': 4.329749101016543e-09}, {'input': [-1.8981131460780302e-17, -1.9950929959484358e-17, -2.088996557026312e-17, -2.1796790368267467e-17, -2.267000609538683e-17, -2.3508266316261922e-17, -2.4310278494390448e-17], 'solu': -1.703078550030273e-17}, {'input': [1.6053287132654793e-27, 1.957018868996554e-27, 2.3056914434791936e-27, 2.6508088088758378e-27, 2.9918388192236584e-27, 3.328255630965036e-27, 3.6595405137602406e-27], 'solu': 2.0711928436950774e-27}, {'input': [7.76073697239889e-16, 7.736785504633876e-16, 7.700904474394118e-16, 7.653149207627537e-16, 7.593593339494109e-16, 7.522328700825806e-16, 7.43

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_32 xx.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_32 xx.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_xx delta x=1 80 delta t=1 40")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{40}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/40)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [0.06964122157899294, 0.06641635128205853, 0.06316587621741183, 0.05989104950506591, 0.056593133653057556, 0.0532734000707264, 0.049933128578562413], 'solu': 0.04679549604668987}, {'input': [-1.9305240549397128e-20, -1.999419621996383e-20, -2.067544374728081e-20, -2.134872049745815e-20, -2.201376690949221e-20, -2.2670326595331484e-20, -2.331814643871886e-20], 'solu': -1.6680688915898662e-20}, {'input': [-0.0003180156618633723, -0.000336547749145829, -0.000354950090864509, -0.0003732155925663752, -0.00039133721255282675, -0.00040930796459439473, -0.0004271209206240783], 'solu': -0.00029160966339428674}, {'input': [-5.750221422069673e-08, -5.929349914833645e-08, -6.106192530335113e-08, -6.28068109237945e-08, -6.45274833230444e-08, -6.622327914913649e-08, -6.789354464049881e-08], 'solu': -4.907370795098545e-08}, {'input': [1.7881995480228325e-17, 1.754755380853704e-17, 1.7206347220819603e-17, 1.6858507258710732e-17, 1.650416802113732e-17, 1.6143466112620524e-17, 1.5776540590612

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [26]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [27]:
list_of_loss_4_file = open('list_of_loss_42 xx.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_42 xx.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [28]:
model_4.save_model("model_xx delta x=1 160 delta t=1 40")